##Transformation from Kafka Messages to Data Cube

This script contains a prototype of a transformation workflow from the intake Kafka messages to the proposed data cube format. It imports data source specific configurations (technical schema, data schema, business logic mapping, etc.) from the 'configurations' notebook and applies them during run-time. The script has been tested using Borg Warner and Dana data and demonstrated to be generic toward both data sources.

###Assumptions adopted in this script:
1. schema of the Kafka json string is validated to match the technical schema 
2. column headers for the data records do not contain periods (which Spark does not like)

###To be completed:
1. Automate loading of technical schema, data schema, and business logic mapping configuration information from postgreSQL tables
2. Automate creating and updating pivot table schema during runtime
3. Implement logic to create a sensor-to-uuid mappings table and update the table whenever a new sensor is seen in realtime
4. Implement mechanism to incrementally update the data cube as the data streams in

###Experiments:
1. Change input Kafka data records from arrays to key-values pairs and compare performance with the current prototype
2. Compare performance on write/read when storing data cube as parquet (read with schema merging) vs json (read with supplied schema)

In [0]:
%run "./configurations"

In [0]:
from pyspark.sql.functions import col, from_json, to_json, concat, lit, window, when, desc, concat_ws, regexp_replace, collect_set
import pyspark.sql.functions as f
from pyspark.sql.window import Window


#**********************************************************************************************************************
# HOUSE KEEPING
#**********************************************************************************************************************

# set the number of shuffle partitions to the total number of cores
spark.conf.set("spark.sql.shuffle.partitions", 8)

# load configuration and other variables through Notebook workflow
#dbutils.notebook.run("./configurations", 60)


#**********************************************************************************************************************
# DATA INGESTION: read stream from Kafka topic
#**********************************************************************************************************************

input_df = (
  spark
  .readStream
  .format("kafka")
  .option("kafka.bootstrap.servers", conf['bootstrap.servers'])
  .option("kafka.security.protocol", "SASL_SSL")
  .option("kafka.sasl.jaas.config", "kafkashaded.org.apache.kafka.common.security.plain.PlainLoginModule required username='{}' password='{}';".format(conf['sasl.username'], conf['sasl.password']))
  .option("kafka.ssl.endpoint.identification.algorithm", "https")
  .option("kafka.sasl.mechanism", "PLAIN")
  .option("subscribe", conf['topic'])
  .option("startingOffsets", conf['startingOffsets'])
  .option("failOnDataLoss", "false")
  .option("maxOffsetsPerTrigger", "1")
  .load()
  .select(col("value").cast("STRING"), col("key").cast("STRING")) 
)


#**********************************************************************************************************************
# TRANSFORM STEP: turn Kafka messages into sensor measurement dataframe
# NOTE: the ingress schema is obtained from 'configurations' notebook, but should be dynamically loaded in production
#
# ASSUMPTIONS:
# 1. schema of the Kafka json string is validated to match the ingress data structure 
# 2. header names do not contain periods (which Spark does not like)
#**********************************************************************************************************************

formatted_df = (input_df
               .select(from_json("value", ingress_schema).alias("ingress_json"))                      # MODIFY for dynamic loading of ingress schema info
               .select(col("ingress_json.headers").alias("headers"), f.explode("ingress_json.data").alias("data"))
               .select(f.arrays_zip("headers", "data").alias("mapped_fields"))
               .select(f.map_from_entries("mapped_fields").alias("mapped_fields"))
               .select(to_json("mapped_fields").alias("json_fields"))
               .select(from_json("json_fields", sensor_data_schema_ddl).alias("sensor_data_json"))  # MODIFY for dynamic loading of data schema info
               .select(col("sensor_data_json.*"))
              )


#**********************************************************************************************************************
# TRANSFORM STEP: apply business logic mapping to incoming data columns
# NOTE: the logic mapping config json is grabbed from 'configurations' notebook in this prototype, but it should be dynamically loaded during production
#**********************************************************************************************************************

processed_df = (formatted_df
               #.na.drop()                        # DISCUSSION: logic to drop rows with null values / NOTE: need to optimize for this step
               .select(regexp_replace(concat_ws('_', *logic_mapping_json["line"]), r'_+', '_').alias("line"),
                       regexp_replace(concat_ws('_', *logic_mapping_json["station_config"]), r'_+', '_').alias("station"), 
                       regexp_replace(concat_ws('_', *logic_mapping_json["sensor_config"]), r'_+', '_').alias("sensor"),
                       regexp_replace(concat_ws('_', *logic_mapping_json["part_number"]), r'_+', '_').alias("part_number"),
                       regexp_replace(concat_ws('_', *logic_mapping_json["serial_number"]), r'_+', '_').alias("serial_number"),
                       col(logic_mapping_json["measured_time"]).alias("timestamp"),
                       *logic_mapping_json["measurement"]
                      )
               .join(sensorDf.select("sensor", "sensor_uuid"), "sensor", "left")
              )


#**********************************************************************************************************************
# TRANSFORM STEP: to prepare for pivot transformation of the data stream, turn table values into key-value pairs
#**********************************************************************************************************************

pivot_prep_df = (processed_df
                 .select(concat(lit('"serial_number":"'), col("serial_number"), lit('"')).alias("serial_number"), 
                         concat(lit('"part_number":"'), col("part_number"), lit('"')).alias("part_number"), 
                         concat(lit('"timestamp":"'), col("timestamp"), lit('"')).alias("timestamp"),
                         concat(lit('"station":"'), col("station"), lit('"')).alias("station"),
                         *[concat(lit('"'), col('sensor_uuid'), lit('_'), lit(m), lit('":"'), col(m), lit('"')).alias(m + '_json') 
                           for m in logic_mapping_json["measurement"]],
                         *[concat(col('sensor_uuid'), lit('_'), lit(m)).alias(m + '_column') 
                           for m in logic_mapping_json["measurement"]]
                        )
                )


#**********************************************************************************************************************
# TRANSFORM STEP: perform pivot transformation of the data stream, collapse records with same timestamp into a single record
# NOTE: logic using watermark potentially needs to be redesigned (alternatively use foreachbatch)
#**********************************************************************************************************************

pivot_df = (pivot_prep_df
            .select(concat_ws(", ", "part_number", "serial_number", "timestamp", "station", *[m+"_json" for m in logic_mapping_json["measurement"]])
                         .alias("json")
                        )
            .select(concat(lit("{"), "json", lit("}")).alias("json"))
            .select(from_json("json", pivot_schema_ddl).alias("schema_json"))
            .select(col("schema_json.*"))
            .withColumn("timestamp", f.to_timestamp("timestamp"))
            .withWatermark("timestamp", "5 seconds")       
            .groupBy("part_number","serial_number", "timestamp")
            .agg(collect_set('station').alias("station_list"), *[f.max(c).alias(c) for c in pivot_feature_cols])
           )


#**********************************************************************************************************************
# RESET STREAMING (for testing and dev only)
# NOTE: uncomment this code block to clear streaming checkpoints and output folders 
#**********************************************************************************************************************

# dbutils.fs.rm(checkpointPath, True)
# dbutils.fs.rm(outputStagingPath, True)
# dbutils.fs.rm(outputPathDir, True)
# dbutils.fs.rm(outputDfRunDir, True)


#**********************************************************************************************************************
# WRITE STAGING RESULTS
# The pivotted results are written to disk, this completes stage 1/2 of the cube transformation. 
# The results will be read back for subsequent steps because the following transformations can only be applied to non-streaming data
#**********************************************************************************************************************

savePivot = (pivot_df
             .writeStream
             .queryName("cube_pivot_to_parquet_staging")
             .trigger(processingTime="30 seconds")
             .format("parquet")
             .option("checkpointLocation", checkpointPath)
             .outputMode("append")
             .start(outputStagingPath)
            )

In [0]:
### for testing, show the generated pivot_df
#display(pivot_load_df)

part_number serial_number timestamp station_list 003a5adb-84ac-42cc-8a40-8ab769e37793_data_value 0135029f-e345-4a01-835a-c9758b114422_data_value 01c7ae65-eb2f-4c3b-adda-47909f3607e0_data_value 01ed8563-f7df-48ba-8f9c-931a770256c6_data_value 0216235c-85b4-4667-85d6-53a9fa0f6497_data_value 029ef063-639d-43f6-b54f-4d94ab869600_data_value 03af25ac-7967-41ae-b6ff-917fe9205358_data_value 04fa520c-4192-4c4b-9a32-1a4e2d49abc9_data_value 05cdcc75-b1be-4e59-9893-47c7ec54eb6c_data_value 05ee1df9-6446-4af9-a7a9-d4c86ce158f8_data_value 06559036-4fd0-45d0-9d58-47c539e52df1_data_value 07ab9bef-b94b-4416-9334-529830aec9c5_data_value 0804e486-ea4e-4904-a813-abc8f92c406b_data_value 080808ff-06f4-4735-baf2-284dc679b258_data_value 09025ee0-8315-4be6-b39c-22cea2d5160b_data_value 0ad7a34f-8dcb-4ffb-a004-73527b40ef42_data_value 0b1cc335-ed4e-419a-84ac-ee58b6d7cc16_data_value 0b34d0b6-e25a-43b3-9115-2aaff8fe5340_data_value 0cdc5a0f-fc46-49af-9481-16a990b0edd5_data_value 0cf2e4fb-f4a1-4209-a36a-47f47854f819_data_value 0d1fa13b-3561-4aaf-96af-90533a1d78cc_data_value 101df26c-c76f-4d3a-8c3f-80a1cb8d86ef_data_value 1038dccf-2c9b-4f24-a90c-7796ec503915_data_value 13371f7e-71b3-44bd-9f07-3830a1e04111_data_value 13c80c14-6567-4563-8473-c5184348246d_data_value 1634fe18-9cca-4c35-9bb5-7a14a919e063_data_value 173005c3-33c5-453e-9e79-fe6df32f0538_data_value 1805a47f-00ff-453e-bc40-ab0efcca70ad_data_value 1988409c-2baa-4966-893e-0d32c8ff15c1_data_value 1991a9ca-1266-4b26-8cb5-8f19eaa29b16_data_value 19d443db-2b71-4b4a-a076-d0de8a39f731_data_value 19f5704f-5462-4b37-a006-28f6242bd5f9_data_value 1b3bdcfd-12e3-4f08-803a-2e4d205ed8fb_data_value 1ba8ab6b-8c02-4188-8a8a-190b47f8a3eb_data_value 1c210ffd-e9ed-4e54-8e12-c08900e56d32_data_value 1cc4335e-e29c-45f2-9b4b-3b131275385e_data_value 1d39fcb7-415f-4c0a-b641-5d46cdb7c912_data_value 1db9643b-f8af-45dd-8a37-684594b977d2_data_value 1fd465ba-9960-4327-8eb6-b107c36b15f9_data_value 206ba4a7-52f1-4e8f-809d-9e63be30cac0_data_value 222973a3-6201-4d6f-a743-8f60b2394b5a_data_value 222c4e58-c585-4b06-a64c-3e3487afe358_data_value 237f76f4-68c5-426b-99c5-57d00ac0f7c1_data_value 24388bc3-5953-4477-9aec-34baba54910c_data_value 257505e2-b113-4021-92a7-430a9695ba75_data_value 284cd4cd-9d0a-4055-ba4c-bf29ebe01526_data_value 2abc23a2-dfa1-4d7a-9355-10bf3bdfcead_data_value 2b3202d0-e0f1-4a12-b8cc-c60ab5df716e_data_value 2c329b38-d4da-414a-bc9c-dc61a543bd8b_data_value 2c85942f-e4a4-415c-bf02-19cc67043356_data_value 2cd12730-d856-45df-a71c-f76e44e65906_data_value 2ddce6ed-e684-416c-ac27-62aa0e623939_data_value 2eb47804-3c56-4c95-b2d6-9b4ff5ea805d_data_value 2fc7b965-7f82-4a1c-8aea-ca67c991b961_data_value 31848ef6-70ca-4581-b0ff-3498df7ebd7d_data_value 32222459-650f-4855-ace1-322e395b5bb1_data_value 329353ca-90d3-4f9b-819f-8da5e4f85b93_data_value 33b95cc6-a368-45e9-8fec-2e29917b4cd1_data_value 3538ccc1-cb81-4001-ad38-37f368137167_data_value 35481747-9994-4e31-af81-bc3ca4c7320a_data_value 35823798-dee4-4bef-8215-a49e22146c9c_data_value 37bb5ee2-0522-4fed-8617-dae672b3a53c_data_value 3848c376-62a7-4d5a-adb2-04ec8299e9d4_data_value 38e08747-be0e-45f2-b2e3-aada414dc1b3_data_value 39cc77c1-e11b-4867-ae60-a16089184bb9_data_value 3a3c8335-11d4-493d-a172-875ace4fbb67_data_value 3aa1943c-4e51-49e7-a203-cde4c5e85fd6_data_value 3b87d8c1-6963-49c0-b100-bcab7a05a8a4_data_value 3c532eb3-f10e-450a-b71c-ece6add00546_data_value 3d99d1ef-8344-408e-8461-c36596e97c64_data_value 3f033066-fde1-46e2-889e-e34b27edf212_data_value 3fc6baf6-ce78-41cd-92a2-8b8890c25a3b_data_value 3fc709f6-7ede-4bbd-9628-074e81d203c9_data_value 419a8623-8796-47e5-a850-fb1b567354b8_data_value 4543750c-fbea-414d-b512-becc15507c1f_data_value 4551dd59-2399-4ac8-8c56-20670c96e5c9_data_value 4637b1ee-6ac3-495a-8023-c6eaae4b9b7b_data_value 463bc312-dbeb-4742-a842-9265bc9092d7_data_value 4807e26e-c867-4112-b5ba-eb5c3ed88a2c_data_value 4d59dc01-7e81-41d7-906a-d616e6547320_data_value 4ea75379-5411-4a71-98de-2996e5dcb000_data_value 572a7408-d5e7-409e-89c5-64b9efb21ed0_data_value 5a2cdf99-b959-4

In [0]:
### This starts stage 2 of the cube transformation. Some transformation steps in this stage are only applicable to non-streaming dataframes
#
# USAGE: for dev and testing, please run the above Stage 1 code for a prolonged period (> 5 min) to ensure adequate data are written to disk
#        before running the Stage 2 code below
#**********************************************************************************************************************


#**********************************************************************************************************************
# READ STAGING RESULTS BACK INTO A STATIC DATAFRAME
#**********************************************************************************************************************

pivot_load_df = spark.read.option("mergeSchema", "true").parquet(outputStagingPath)


#**********************************************************************************************************************
# DEFINE WINDOWS FOR AGGREGATION
#**********************************************************************************************************************

w1 = Window.partitionBy(["part_number", "serial_number"]).orderBy("timestamp")
w2 = Window.partitionBy(["part_number", "serial_number", "station"]).orderBy("timestamp")
w3 = Window.partitionBy(["part_number", "serial_number", "station", "consecutive_idx"]).orderBy(f.desc("timestamp"))
w4 = Window.partitionBy(["part_number", "serial_number"]).rowsBetween(Window.unboundedPreceding,Window.unboundedFollowing)
w5 = Window.partitionBy(["part_number", "serial_number", "target_operation"]).orderBy("target_test_date")


#**********************************************************************************************************************
# TRANSFORM STEP: add derived columns to prepare for path extraction
#
# New column details:
# 1. op_order: order of operations for a part goes through the assembly line, starting from 1 for the first operation
# 2. op_rerun: # of times a part passes a station
# 3. consecutive_idx (TEMPORARY): consecutive visits of a part to the same station (i.e. no other station in between) have the same consecutive_idx
# 4. is_last_measure: if a part is consecutively measured at a station, only the last measurement have is_last_measure = 1
#**********************************************************************************************************************

run_order_df = (pivot_load_df
                .withColumn("station", f.element_at("station_list", 1))
                .withColumn("op_order", f.dense_rank().over(w1))
                .withColumn("op_rerun", f.dense_rank().over(w2))
                .withColumn("consecutive_idx", col("op_order")-col("op_rerun"))
                .withColumn("is_last_measure", f.dense_rank().over(w3))
                .select("part_number", "serial_number", "station", "timestamp", "op_order", "op_rerun", "is_last_measure", *pivot_feature_cols)
               )


#**********************************************************************************************************************
# TRANSFORM STEP: identify 'path'(s) for each unit
#
# OUTPUT:  a dataframe with one row for each 'path', identified by 
#          1) the part and serial number of the assembled unit (part_number, serial_number)
#          2) the target station and the corresponding test date (target_operation, target_test_date)
#          3) a pass (1)/fail (0) flag indicating whether the part passed or failed at the target station (pass_fail)
#          4) a run number indicating the number of attempts for the unit to reach the target station
#**********************************************************************************************************************

target_ops_df = (run_order_df.withColumn("max_op_order", f.max("op_order").over(w4))
                      .filter((col("station")==target) & (col("is_last_measure")==1))
                      .withColumn("max_target_rerun", f.max("op_rerun").over(w4))
                      .withColumn("pass_fail", f.when(col("op_order")==col("max_op_order"), 2)
                                                 .when(col("op_rerun")==col("max_target_rerun"), 1)
                                                 .when(col("op_rerun")<col("max_target_rerun"), 0)
                                                 .otherwise(-1)
                                 )
                      .select("part_number", "serial_number", "station", "timestamp", "pass_fail")
                      .withColumnRenamed("timestamp", "target_test_date")
                      .withColumnRenamed("station", "target_operation")
                      .withColumn("run_number", f.row_number().over(w5))
                     )


#**********************************************************************************************************************
# TRANSFORM STEP: associate the pivotted sensor measurements to their corresponding path
#**********************************************************************************************************************

target_ops_df.registerTempTable("target_ops")
run_order_df.registerTempTable("run_order")
join_target_with_ops_sql = f"""
select o.part_number as part_number, o.serial_number as serial_number, run_number, 
    pass_fail, station, timestamp, `{'`,`'.join(pivot_feature_cols)}`,
	dense_rank() over (
		partition by o.part_number, o.serial_number, target_test_date, station order by timestamp
	) as op_rerun_in_path
from target_ops o join run_order r 
on o.part_number=r.part_number and o.serial_number=r.serial_number and target_test_date>=timestamp 
"""
cube_df= spark.sql(join_target_with_ops_sql)


#**********************************************************************************************************************
# WRITE CUBE TO DISK
# Write cube dataframe to parquet on disk. This completes the cube transformation.
#**********************************************************************************************************************

saveCube = cube_df.write.parquet(outputPathDir)  

In [0]:
### for testing, show the generated cube_df
display(cube_df)

part_number serial_number run_number pass_fail station timestamp 003a5adb-84ac-42cc-8a40-8ab769e37793_data_value 0135029f-e345-4a01-835a-c9758b114422_data_value 01c7ae65-eb2f-4c3b-adda-47909f3607e0_data_value 01ed8563-f7df-48ba-8f9c-931a770256c6_data_value 0216235c-85b4-4667-85d6-53a9fa0f6497_data_value 029ef063-639d-43f6-b54f-4d94ab869600_data_value 03af25ac-7967-41ae-b6ff-917fe9205358_data_value 04fa520c-4192-4c4b-9a32-1a4e2d49abc9_data_value 05cdcc75-b1be-4e59-9893-47c7ec54eb6c_data_value 05ee1df9-6446-4af9-a7a9-d4c86ce158f8_data_value 06559036-4fd0-45d0-9d58-47c539e52df1_data_value 07ab9bef-b94b-4416-9334-529830aec9c5_data_value 0804e486-ea4e-4904-a813-abc8f92c406b_data_value 080808ff-06f4-4735-baf2-284dc679b258_data_value 09025ee0-8315-4be6-b39c-22cea2d5160b_data_value 0ad7a34f-8dcb-4ffb-a004-73527b40ef42_data_value 0b1cc335-ed4e-419a-84ac-ee58b6d7cc16_data_value 0b34d0b6-e25a-43b3-9115-2aaff8fe5340_data_value 0cdc5a0f-fc46-49af-9481-16a990b0edd5_data_value 0cf2e4fb-f4a1-4209-a36a-47f47854f819_data_value 0d1fa13b-3561-4aaf-96af-90533a1d78cc_data_value 101df26c-c76f-4d3a-8c3f-80a1cb8d86ef_data_value 1038dccf-2c9b-4f24-a90c-7796ec503915_data_value 13371f7e-71b3-44bd-9f07-3830a1e04111_data_value 13c80c14-6567-4563-8473-c5184348246d_data_value 1634fe18-9cca-4c35-9bb5-7a14a919e063_data_value 173005c3-33c5-453e-9e79-fe6df32f0538_data_value 1805a47f-00ff-453e-bc40-ab0efcca70ad_data_value 1988409c-2baa-4966-893e-0d32c8ff15c1_data_value 1991a9ca-1266-4b26-8cb5-8f19eaa29b16_data_value 19d443db-2b71-4b4a-a076-d0de8a39f731_data_value 19f5704f-5462-4b37-a006-28f6242bd5f9_data_value 1b3bdcfd-12e3-4f08-803a-2e4d205ed8fb_data_value 1ba8ab6b-8c02-4188-8a8a-190b47f8a3eb_data_value 1c210ffd-e9ed-4e54-8e12-c08900e56d32_data_value 1cc4335e-e29c-45f2-9b4b-3b131275385e_data_value 1d39fcb7-415f-4c0a-b641-5d46cdb7c912_data_value 1db9643b-f8af-45dd-8a37-684594b977d2_data_value 1fd465ba-9960-4327-8eb6-b107c36b15f9_data_value 206ba4a7-52f1-4e8f-809d-9e63be30cac0_data_value 222973a3-6201-4d6f-a743-8f60b2394b5a_data_value 222c4e58-c585-4b06-a64c-3e3487afe358_data_value 237f76f4-68c5-426b-99c5-57d00ac0f7c1_data_value 24388bc3-5953-4477-9aec-34baba54910c_data_value 257505e2-b113-4021-92a7-430a9695ba75_data_value 284cd4cd-9d0a-4055-ba4c-bf29ebe01526_data_value 2abc23a2-dfa1-4d7a-9355-10bf3bdfcead_data_value 2b3202d0-e0f1-4a12-b8cc-c60ab5df716e_data_value 2c329b38-d4da-414a-bc9c-dc61a543bd8b_data_value 2c85942f-e4a4-415c-bf02-19cc67043356_data_value 2cd12730-d856-45df-a71c-f76e44e65906_data_value 2ddce6ed-e684-416c-ac27-62aa0e623939_data_value 2eb47804-3c56-4c95-b2d6-9b4ff5ea805d_data_value 2fc7b965-7f82-4a1c-8aea-ca67c991b961_data_value 31848ef6-70ca-4581-b0ff-3498df7ebd7d_data_value 32222459-650f-4855-ace1-322e395b5bb1_data_value 329353ca-90d3-4f9b-819f-8da5e4f85b93_data_value 33b95cc6-a368-45e9-8fec-2e29917b4cd1_data_value 3538ccc1-cb81-4001-ad38-37f368137167_data_value 35481747-9994-4e31-af81-bc3ca4c7320a_data_value 35823798-dee4-4bef-8215-a49e22146c9c_data_value 37bb5ee2-0522-4fed-8617-dae672b3a53c_data_value 3848c376-62a7-4d5a-adb2-04ec8299e9d4_data_value 38e08747-be0e-45f2-b2e3-aada414dc1b3_data_value 39cc77c1-e11b-4867-ae60-a16089184bb9_data_value 3a3c8335-11d4-493d-a172-875ace4fbb67_data_value 3aa1943c-4e51-49e7-a203-cde4c5e85fd6_data_value 3b87d8c1-6963-49c0-b100-bcab7a05a8a4_data_value 3c532eb3-f10e-450a-b71c-ece6add00546_data_value 3d99d1ef-8344-408e-8461-c36596e97c64_data_value 3f033066-fde1-46e2-889e-e34b27edf212_data_value 3fc6baf6-ce78-41cd-92a2-8b8890c25a3b_data_value 3fc709f6-7ede-4bbd-9628-074e81d203c9_data_value 419a8623-8796-47e5-a850-fb1b567354b8_data_value 4543750c-fbea-414d-b512-becc15507c1f_data_value 4551dd59-2399-4ac8-8c56-20670c96e5c9_data_value 4637b1ee-6ac3-495a-8023-c6eaae4b9b7b_data_value 463bc312-dbeb-4742-a842-9265bc9092d7_data_value 4807e26e-c867-4112-b5ba-eb5c3ed88a2c_data_value 4d59dc01-7e81-41d7-906a-d616e6547320_data_value 4ea75379-5411-4a71-98de-2996e5dcb000_data_value 572a7408-d5e7-409e-89c5-64b9efb21ed0_data_value